<a href="https://colab.research.google.com/github/xalixja/FODS/blob/main/Projekt.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Understanding and Detecting Malicious Prompts Using Embeddings, Clustering, and Classification
## Fundamentals of Data Science Project
## Author: Alicja Borek


##1. Data Loading and Basic Preprocessing:

In [ ]:
#@inproceedings{plguard2025,
#  author    = {Krasnodębska, Aleksandra and Seweryn, Karolina and Łukasik, Szymon and Kusa, Wojciech},
#  title     = {{PL-Guard: Benchmarking Language Model Safety for Polish}},
#  booktitle = {Proceedings of the 10th Workshop on Slavic Natural Language Processing},
#  year      = {2025},
#  address   = {Vienna, Austria},
#  publisher = {Association for Computational Linguistics}
#}

import pandas as pd
import numpy as np

#loading test data
df = pd.read_parquet('data.parquet')
len(df.index) #900 rows
df.head()

text     category
0  Jako model językowy nie posiadam wiedzy na tem...         safe
1  Oto kilka sugestii, które mogą pomóc w stworze...  unsafe\nS12
2  Przedstawianie się jako przedstawiciel banku l...   unsafe\nS2
3  Zastosowanie utworu muzycznego w reklamie bez ...   unsafe\nS8
4  **Rozpowszechnianie fałszywych oskarżeń o nadu...   unsafe\nS6

In [ ]:
#loading adversarial data
df_a = pd.read_parquet('data_adversarial.parquet')
df_a.head()

original_text     category  \
0  Jako model językowy nie posiadam wiedzy na tem...         safe   
1  Oto kilka sugestii, które mogą pomóc w stworze...  unsafe\nS12   
2  Przedstawianie się jako przedstawiciel banku l...   unsafe\nS2   
3  Zastosowanie utworu muzycznego w reklamie bez ...   unsafe\nS8   
4  **Rozpowszechnianie fałszywych oskarżeń o nadu...   unsafe\nS6   

                                                text  num_changes  \
0  Jako model jzeykowy nie posiadam wiedzy na tem...            6   
1  Oto klika sugestii, ktore moga pomoc ws tworze...           20   
2  Przedstawianie sie jako przedstawiciel banku l...            1   
3  Zastosowanie utworu muzycznego w reklamie bez ...           20   
4  **Rozpowszechnianie falszywy)h oskarzen o nadu...           15   

                                  modification_types  
0  ['swap', 'delete', 'keyboard', 'diacritic', 's...  
1  ['swap', 'swap', 'swap', 'diacritic', 'insert'...  
2                                      ['diacritic']  
3  ['ocr', 'substitute', 'substitute', 'insert', ...  
4  ['diacritic', 'keyboard', 'diacritic', 'substi...

In [32]:
#basic preprocessing

df.isnull().values.any() #making sure that there are not any missing values

#normalization
df['text'] = df['text'].str.lower() #all texts in lowercase
df['text'] = df['text'].str.replace(r'[^\w\s]+', '', regex=True) #deleting punctuation or other special characters

#sample length reduction
print(df['text'].str.len().max())
#im leaving these to embedding model

df.head()

3771


text     category    bert_x  \
0  jako model językowy nie posiadam wiedzy na tem...         safe -0.228982   
1  oto kilka sugestii które mogą pomóc w stworzen...  unsafe\nS12 -0.094701   
2  przedstawianie się jako przedstawiciel banku l...   unsafe\nS2 -0.257582   
3  zastosowanie utworu muzycznego w reklamie bez ...   unsafe\nS8 -0.228160   
4  rozpowszechnianie fałszywych oskarżeń o naduży...   unsafe\nS6 -0.177737   

     bert_y   spacy_x   spacy_y  bert_tsne_x  bert_tsne_y  spacy_tsne_x  \
0 -0.228366  0.259107 -0.102037   -36.937286   -46.065414      0.991862   
1  0.077975  0.081632  0.060320    -6.459249   -48.532860     -9.028530   
2  0.189821  0.210704  0.020083   -27.040176    -6.377265    -26.751686   
3 -0.129311  0.146133 -0.064759    11.935987   -57.603695     11.825717   
4  0.145022  0.162799 -0.158445   -32.653919    19.869923     12.662413   

   spacy_tsne_y  bert_umap_x  bert_umap_y  spacy_umap_x  spacy_umap_y  \
0    -41.450794     5.374025     6.439055      8.037679     10.867112   
1     -1.722406     6.141762     4.948128      9.043536      8.876700   
2    -70.834679     8.455338     7.550086      6.527307     10.355415   
3    -36.182537     6.036556     5.481096      8.586397     10.538047   
4    -18.022030     8.155779     7.663217      8.182815      7.729810   

  simple_category  
0            Safe  
1          Unsafe  
2          Unsafe  
3          Unsafe  
4          Unsafe

##2. Text Representation: Using Embeddings

In [ ]:
!pip install sentence-transformers

DEPRECATION: Loading egg at /usr/local/lib/python3.12/dist-packages/fasttext-0.9.2-py3.12-linux-x86_64.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation. Discussion can be found at https://github.com/pypa/pip/issues/12330


In [ ]:
#i will do two vectors one using BERT and other using SpaCy so later i can check which is doing better job

#BERT - dynamic model, reading the sentence and understand context

#my first approuch was with bert_base_uncased but this model knows only english
#and with tokens

from sentence_transformers import SentenceTransformer

#model which understands many languages (including polish) and returns one punct for the whole sentence by pooling results of all words
model_bert = SentenceTransformer('paraphrase-multilingual-MiniLM-L12-v2')
#MOZE JESZCZE SPROBOWAC INNEGO MODELU BERTA

#embeddings for column text
embeddings_bert = model_bert.encode(df['text'].tolist(), show_progress_bar=True) #np matrix

#verify the results
print(f"We have {embeddings_bert.shape[0]} texts and all of them are vectors of {embeddings_bert.shape[1]} numbers.")

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Batches:   0%|          | 0/29 [00:00<?, ?it/s]

We have 900 texts and all of them are vectors of 384 numbers.


In [ ]:
!pip install spacy
!python -m spacy download pl_core_news_lg

DEPRECATION: Loading egg at /usr/local/lib/python3.12/dist-packages/fasttext-0.9.2-py3.12-linux-x86_64.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation. Discussion can be found at https://github.com/pypa/pip/issues/12330
DEPRECATION: Loading egg at /usr/local/lib/python3.12/dist-packages/fasttext-0.9.2-py3.12-linux-x86_64.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation. Discussion can be found at https://github.com/pypa/pip/issues/12330
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 573.7/573.7 MB 729.2 kB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('pl_core_news_lg')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart run

In [11]:
#spaCy - static model

#at first i was trying to use FastText but this model was to big for my possibilities so instead i used polish model SpaCy which is similar
#to FastText but not as large

import spacy

#polish model large version
nlp = spacy.load("pl_core_news_lg")

#embeddings for column text
embeddings_spacy_list = df['text'].apply(lambda x: nlp(x).vector).tolist()

embeddings_spacy = np.array(embeddings_spacy_list) #np matrix

#verify the results
print(f"We have {embeddings_spacy.shape[0]} texts and all of them are vectors of {embeddings_spacy.shape[1]} numbers.")

We have 900 texts and all of them are vectors of 300 numbers.


In [12]:
#checking if data types are the same
print(f"Type of BERT data: {type(embeddings_bert)}")
print(f"Type of spaCy data: {type(embeddings_spacy)}")

Typ danych BERT: <class 'numpy.ndarray'>
Typ danych spaCy: <class 'numpy.ndarray'>


##3. Dimensionality Reduction (PCA, t-SNE, UMAP)

In [18]:
#i will reduce dimensions from 384 in bert vector and 300 in spacy vector to 2d

#pca
#we dont have to standarize our data because we have only one unit - prompts

from sklearn.decomposition import PCA
from sklearn.preprocessing import normalize

#normalization - all vectors have length = 1
embeddings_bert_norm = normalize(embeddings_bert)
embeddings_spacy_norm = normalize(embeddings_spacy)

#i chose 2d data because they will be easier to read in report

#PCA for BERT
pca_bert = PCA(n_components=2)
bert_2d = pca_bert.fit_transform(embeddings_bert_norm)

#PCA for spaCy
pca_spacy = PCA(n_components=2)
spacy_2d = pca_spacy.fit_transform(embeddings_spacy_norm)

#saving the results
df['bert_x'] = bert_2d[:, 0]
df['bert_y'] = bert_2d[:, 1]

df['spacy_x'] = spacy_2d[:, 0]
df['spacy_y'] = spacy_2d[:, 1]

#verify the results
print(bert_2d.shape)
print(spacy_2d.shape)
print("We have ready pca coordinates")

#pca_bert quality
print("BERT:")
print("Latent array:", pca_bert.explained_variance_ratio_)
print("Cumulative:", np.cumsum(pca_bert.explained_variance_ratio_))

#pca_spacy quality
print("spaCy:")
print("Latent array:", pca_spacy.explained_variance_ratio_)
print("Cumulative:", np.cumsum(pca_spacy.explained_variance_ratio_))

print(f"BERT (Contextual Embeddings): The first two components explain only {np.cumsum(pca_bert.explained_variance_ratio_)[1]*100}% of the total variance.")
print(f"spaCy (Static Embeddings): The first two components explain approximately {np.cumsum(pca_spacy.explained_variance_ratio_)[1]*100}% of the total variance.")

(900, 2)
(900, 2)
We have ready 2D data
BERT:
Latent array: [0.07617836 0.06866631]
Cumulative: [0.07617836 0.14484467]
spaCy:
Latent array: [0.14571595 0.09707098]
Cumulative: [0.14571595 0.24278694]
BERT (Contextual Embeddings): The first two components explain only 14.484466552734375% of the total variance.
spaCy (Static Embeddings): The first two components explain approximately 24.27869415283203% of the total variance.


text     category    bert_x  \
0  jako model językowy nie posiadam wiedzy na tem...         safe -0.228982   
1  oto kilka sugestii które mogą pomóc w stworzen...  unsafe\nS12 -0.094701   
2  przedstawianie się jako przedstawiciel banku l...   unsafe\nS2 -0.257582   
3  zastosowanie utworu muzycznego w reklamie bez ...   unsafe\nS8 -0.228160   
4  rozpowszechnianie fałszywych oskarżeń o naduży...   unsafe\nS6 -0.177737   

     bert_y   spacy_x   spacy_y  
0 -0.228366  0.259107 -0.102037  
1  0.077975  0.081632  0.060320  
2  0.189821  0.210704  0.020083  
3 -0.129311  0.146133 -0.064759  
4  0.145022  0.162799 -0.158445

In [49]:
#t-sne

from sklearn.manifold import TSNE

#different parameters for different models
tsne_model_spacy = TSNE(n_components=2, random_state=42, perplexity=30, max_iter=1000)
tsne_model = TSNE(n_components=2, random_state=42, perplexity=30, max_iter=3000, init = 'pca', learning_rate=500, metric='cosine')

bert_tsne = tsne_model.fit_transform(embeddings_bert_norm)
spacy_tsne = tsne_model_spacy.fit_transform(embeddings_spacy_norm)

df['bert_tsne_x'] = bert_tsne[:, 0]
df['bert_tsne_y'] = bert_tsne[:, 1]
df['spacy_tsne_x'] = spacy_tsne[:, 0]
df['spacy_tsne_y'] = spacy_tsne[:, 1]

print("We have ready t-sne coordinates")

We have ready t-sne coordinates


In [22]:
!pip install umap-learn

DEPRECATION: Loading egg at /usr/local/lib/python3.12/dist-packages/fasttext-0.9.2-py3.12-linux-x86_64.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation. Discussion can be found at https://github.com/pypa/pip/issues/12330


In [58]:
#umap

import umap

reducer_spacy = umap.UMAP(n_neighbors=15, min_dist=0.1, random_state=42, metric='euclidean')
reducer = umap.UMAP(n_neighbors=15, min_dist=0.0, random_state=42, metric='cosine')

bert_umap = reducer.fit_transform(embeddings_bert_norm)
spacy_umap = reducer_spacy.fit_transform(embeddings_spacy_norm)

df['bert_umap_x'] = bert_umap[:, 0]
df['bert_umap_y'] = bert_umap[:, 1]
df['spacy_umap_x'] = spacy_umap[:, 0]
df['spacy_umap_y'] = spacy_umap[:, 1]

print("We have ready umap coordinates")

/usr/local/lib/python3.12/dist-packages/umap/umap_.py:1952: UserWarning:

n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.

/usr/local/lib/python3.12/dist-packages/umap/umap_.py:1952: UserWarning:

n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.



We have ready umap coordinates


##4. Visualizing the Dataset (Interactive Plot)

In [56]:
import plotly.express as px

#list of ours embeddings with various dimension reduction
configs = [
    # ("BERT - PCA", 'bert_x', 'bert_y'),
    # ("BERT - t-SNE", 'bert_tsne_x', 'bert_tsne_y'),
    ("BERT - UMAP", 'bert_umap_x', 'bert_umap_y'),
    # ("spaCy - PCA", 'spacy_x', 'spacy_y'),
    # ("spaCy - t-SNE", 'spacy_tsne_x', 'spacy_tsne_y'),
    ("spaCy - UMAP", 'spacy_umap_x', 'spacy_umap_y'),
]

for title, x_col, y_col in configs:
    fig = px.scatter(
        df,
        x=x_col,
        y=y_col,
        color='category',
        hover_data=['text'],
        title=title,
        color_discrete_map={'safe': 'green'},
        template='plotly_white',
        opacity=0.6,
        width=800, height=600
    )

    #we dont need axes because we dont have concrete values
    #for us distant is the most important ascept
    fig.update_xaxes(visible=False)
    fig.update_yaxes(visible=False)

    fig.show()

In [59]:
#simplified view

SAFE_LABEL = 'safe'

# Tworzymy nową, prostszą kolumnę: "Safe" vs "Toxic"
df['simple_category'] = df['category'].apply(lambda x: 'Safe' if x == SAFE_LABEL else 'Unsafe')

for title, x_col, y_col in configs:
  fig = px.scatter(
      df,
      x=x_col,
      y=y_col,
      color='simple_category',
      hover_data=['text', 'category'],
      title=title,
      template='plotly_white',
      color_discrete_map={'Safe': 'green', 'Unsafe': 'red'},
      opacity=0.6,
      width=800, height=600
  )

  fig.update_xaxes(visible=False)
  fig.update_yaxes(visible=False)

  fig.show()